# 気象庁のレーダーデータをダウンロードしてプロットする

## １．ダウンロードのための準備

In [5]:
import os
import requests
import glob
import subprocess
import tarfile

%cd C:/Users/mori/Documents/PythonData/

def getradar(datehour, n10):
    datehour = str(datehour)

    n10 = str(n10)
    %cd C:/Users/mori/Documents/PythonData/
    fname = f"Z__C_RJTD_{datehour}{n10}000_RDR_JMAGPV__grib2.tar"
    url = f"http://database.rish.kyoto-u.ac.jp/arch/jmadata/data/jma-radar/synthetic/original/{datehour[0:4]}/{datehour[4:6]}/{datehour[6:8]}/Z__C_RJTD_{datehour}{n10}000_RDR_JMAGPV__grib2.tar"

    if not os.path.exists(f"./{fname}"):
        response = requests.get(url)
        if response.status_code == 200:
            # ファイルを書き込み
            with open(f"./{fname}", 'wb') as file:
                file.write(response.content)
            print(f"{fname} has been downloaded.")
            with tarfile.open( fname, 'r') as tar:
                # 指定したディレクトリに展開
                tar.extractall(path='.')
        else:
            print("Failed to download the file.")
    else:
        print(f"{fname} already exists.")

    bin_files = glob.glob(os.path.join('.', '*.bin'))
 
    for bin_file in bin_files:
        # 同じ名前の *.ncdf ファイル名を生成
        ncdf_file = bin_file.replace('.bin', '.ncdf')
        #
        # *.ncdf ファイルが存在するかチェック
        if not os.path.exists(ncdf_file):
            print(f"Converting {bin_file} to {ncdf_file}")
            # コマンドを実行 (例: wgrib2 file.bin -netcdf file.ncdf)
            command = f"wgrib2 {bin_file} -netcdf {ncdf_file}"
            subprocess.run(command, shell=True)
        # else:
        #    print(f"{ncdf_file} already exists.")

C:\Users\mori\Documents\PythonData


In [14]:
for day in range(1,5):
    for hour in range(24):
        for x in range(6):
            getradar(2023070000+day*100+hour,x);

C:\Users\mori\Documents\PythonData
Z__C_RJTD_20230701000000_RDR_JMAGPV__grib2.tar already exists.
C:\Users\mori\Documents\PythonData
Z__C_RJTD_20230701001000_RDR_JMAGPV__grib2.tar already exists.
C:\Users\mori\Documents\PythonData
Z__C_RJTD_20230701002000_RDR_JMAGPV__grib2.tar already exists.
C:\Users\mori\Documents\PythonData
Z__C_RJTD_20230701003000_RDR_JMAGPV__grib2.tar already exists.
C:\Users\mori\Documents\PythonData
Z__C_RJTD_20230701004000_RDR_JMAGPV__grib2.tar already exists.
C:\Users\mori\Documents\PythonData
Z__C_RJTD_20230701005000_RDR_JMAGPV__grib2.tar already exists.
C:\Users\mori\Documents\PythonData
Z__C_RJTD_20230701010000_RDR_JMAGPV__grib2.tar already exists.
C:\Users\mori\Documents\PythonData
Z__C_RJTD_20230701011000_RDR_JMAGPV__grib2.tar already exists.
C:\Users\mori\Documents\PythonData
Z__C_RJTD_20230701012000_RDR_JMAGPV__grib2.tar already exists.
C:\Users\mori\Documents\PythonData
Z__C_RJTD_20230701013000_RDR_JMAGPV__grib2.tar already exists.
C:\Users\mori\Docume

In [6]:
import xarray as xr
import matplotlib.pyplot as plt
import cartopy.crs as ccrs
import cartopy.feature as cfeature
import traceback
import numpy as np
import math

def drawIntensity(datehour, n10, lat_range, lon_range, save_path=None):
    # 保存先のファイルが既に存在するかを確認
    if save_path and os.path.exists(save_path):
        print(f"保存先のファイルが既に存在します: {save_path}")
        return

    # 正しいファイルパスを生成
    filepath = f"C:/Users/mori/Documents/PythonData/Z__C_RJTD_{datehour}{n10}000_RDR_JMAGPV_Ggis1km_Prr10lv_ANAL_grib2.ncdf"
    # print(filepath)

    # タイトル用の日時文字列を生成
    date_str = str(datehour)
    title_str = f"RADAR Intensity {date_str[:4]}-{date_str[4:6]}-{date_str[6:8]} {date_str[8:10]}:{n10}0"

    try:
        with xr.open_dataset(filepath) as dataset:
            data = dataset['var0_1_201_surface']
            lat  = dataset['latitude']
            lon  = dataset['longitude']

            # 描画用の図と軸の設定
            fig, ax = plt.subplots(figsize=(10, 10), subplot_kw={'projection': ccrs.PlateCarree()})
            ax.set_extent([lon_range[0], lon_range[1], lat_range[0], lat_range[1]], crs=ccrs.PlateCarree())

            # ゼロ値を小さな値に置き換え、対数変換する
            data_with_offset = np.where(data[0,:,:] <= 0, 1e-10, data[0,:,:])
            log_data = np.log2(data_with_offset)

            min_level = -1
            max_level =  7
            level_number = 9
            levels = np.linspace(min_level, max_level, level_number)

            # データの描画
            contour = ax.contourf(lon, lat, log_data, levels=levels, transform=ccrs.PlateCarree(), zorder=0)
            plt.colorbar(contour, ax=ax, shrink=0.5, label='Intensity')

            # 海岸線の描画
            ax.coastlines(color='white', linewidth=2)
            ax.add_feature(cfeature.BORDERS, linestyle=':', edgecolor='gray')
            ax.add_feature(cfeature.LAND, edgecolor='black')
            ax.add_feature(cfeature.OCEAN)

            # グリッドラインの追加
            ax.gridlines(draw_labels=True, dms=True, x_inline=False, y_inline=False)

            # 軸ラベルの設定
            plt.xlabel('Longitude')
            plt.ylabel('Latitude')

            # タイトルの追加
            plt.title(title_str)

            # 図を表示する前にPNG形式で保存
            if save_path:
                plt.savefig(save_path, format='png', dpi=300)
                plt.close()  # 図を保存した後に閉じる
            else:
                plt.show()

    except FileNotFoundError:
        print(f"ファイルが見つかりません: {filepath}")
        traceback.print_exc()  # ここでスタックトレースを表示

    except Exception as e:
        print(f"データの読み込み中にエラーが発生しました: {e}")
        
    # 不要なオブジェクトの削除
    del dataset

In [ ]:
for day in range(1,5):
    for hour in range(24):
        datehour=2023070000+day*100+hour
        for n10 in range(6):
            fpath=f"C:/Users/mori/Documents/PythonData/figs/{datehour}{n10}0.png"
            drawIntensity(datehour,n10,(29,35), (127,133),fpath)

保存先のファイルが既に存在します: C:/Users/mori/Documents/PythonData/figs/202307010000.png
保存先のファイルが既に存在します: C:/Users/mori/Documents/PythonData/figs/202307010010.png
保存先のファイルが既に存在します: C:/Users/mori/Documents/PythonData/figs/202307010020.png
保存先のファイルが既に存在します: C:/Users/mori/Documents/PythonData/figs/202307010030.png
保存先のファイルが既に存在します: C:/Users/mori/Documents/PythonData/figs/202307010040.png
保存先のファイルが既に存在します: C:/Users/mori/Documents/PythonData/figs/202307010050.png
保存先のファイルが既に存在します: C:/Users/mori/Documents/PythonData/figs/202307010100.png
保存先のファイルが既に存在します: C:/Users/mori/Documents/PythonData/figs/202307010110.png
保存先のファイルが既に存在します: C:/Users/mori/Documents/PythonData/figs/202307010120.png
保存先のファイルが既に存在します: C:/Users/mori/Documents/PythonData/figs/202307010130.png
保存先のファイルが既に存在します: C:/Users/mori/Documents/PythonData/figs/202307010140.png
保存先のファイルが既に存在します: C:/Users/mori/Documents/PythonData/figs/202307010150.png
保存先のファイルが既に存在します: C:/Users/mori/Documents/PythonData/figs/202307010200.png
保存先のファイルが既に存在します: C:/User